In [1]:
import os
import glob
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import datetime
import warnings
warnings.filterwarnings("ignore")
pd.set_option("display.max_columns", None)

from sklearn.cluster import KMeans
import plotly.express as px
import plotly.graph_objects as go

from sklearn.metrics import silhouette_score
from sklearn.preprocessing import RobustScaler

In [2]:
def skim(data):
    print(f'''number of rows: {data.shape[0]}''')
#number of columns: {data.shape[1]}''')
    summary = pd.DataFrame({
                    'column': data.columns.values,
                    'type': data.dtypes.values,
                    'n_unique': data.nunique().values,
                    'n_missing': data.isna().sum().reset_index()[0],
                    'pct_missing': round(data.isna().sum().reset_index()[0]/len(data)*100, 2),
                    'min': data.dropna().min().values,
                    'max': data.dropna().max().values
                })
    return summary

In [3]:
master_data = pd.read_csv("../data/processed/master_data.csv", engine="pyarrow")
skim(master_data)

number of rows: 107855


column            type  n_unique  n_missing  \
0              customer_unique_id          object     96096          0   
1                     customer_id          object     99441          0   
2        customer_zip_code_prefix           int64     14994          0   
3                   customer_city          object      4119          0   
4                  customer_state          object        27          0   
5                        order_id          object     99441          0   
6                    order_status          object         8          0   
7        order_purchase_timestamp  datetime64[ns]     98875          0   
8               order_approved_at  datetime64[ns]     90747        161   
9    order_delivered_carrier_date  datetime64[ns]     81020       1905   
10  order_delivered_customer_date  datetime64[ns]     95671       3164   
11  order_estimated_delivery_date          object       459          0   
12                     product_id          object     32952          0   
13                      seller_id          object      3096          0   
14                          price         float64      5968        830   
15               order_item_count         float64        16          0   
16          product_category_name          object        72          0   
17  product_category_name_english          object        72          0   
18             payment_sequential         float64        29          0   
19                   payment_type          object         5          0   
20           payment_installments         float64        23          0   
21                  payment_value         float64     29077          0   
22                   review_score          object         6          0   

    pct_missing                               min  \
0          0.00  0000366f3b9a7992bf8c76cfdf3221e2   
1          0.00  00012a2ce6f8dcda20d059ce98491703   
2          0.00                              1003   
3          0.00               abadia dos dourados   
4          0.00                                AC   
5          0.00  00010242fe8c5a6d1ba2dd792cb16214   
6          0.00                          canceled   
7          0.00               2016-09-15 12:16:38   
8          0.15               2016-09-15 12:16:38   
9          1.77               2016-10-08 10:34:01   
10         2.93               2016-10-11 13:46:32   
11         0.00                        2016-10-04   
12         0.00  00066f42aeeb9f3007548bb9d3f33c38   
13         0.00  0015a82c2db000af6aaaf3ae2ecb0532   
14         0.77                              0.85   
15         0.00                               1.0   
16         0.00         agro_industria_e_comercio   
17         0.00        agro_industry_and_commerce   
18         0.00                               1.0   
19         0.00                            boleto   
20         0.00                               1.0   
21         0.00                               0.0   
22         0.00                               1.0   

                                 max  
0   ffffd2657e2aad2907e67c3e9daecbeb  
1   ffffa3172527f765de70084a7e53aae8  
2                              99980  
3                             zortea  
4                                 TO  
5   fffe41c64501cc87c801fd61db3f6244  
6                          delivered  
7                2018-08-29 15:00:37  
8                2018-08-29 15:10:26  
9                2018-09-11 19:48:28  
10               2018-10-17 13:22:46  
11                        2018-10-25  
12  fffe9eeff12fcbd74a2f2b007dde0c58  
13  ffff564a4f9085cd26170f4732393726  
14                            6735.0  
15                              20.0  
16             utilidades_domesticas  
17                     watches_gifts  
18                              26.0  
19                           voucher  
20                              24.0  
21                          13664.08  
22                           unknown

In [4]:
customer_activity = master_data.groupby(["customer_unique_id", "customer_id", "order_id", "order_status", "order_purchase_timestamp", "payment_sequential", "payment_value"], as_index=False)[["order_item_count"]].agg("sum").sort_values(by=["order_purchase_timestamp", "order_id"], ignore_index=True)
master_data[["order_purchase_timestamp", "order_item_count", "payment_value"]].describe().T

count                           mean  \
order_purchase_timestamp    107855  2017-12-29 22:42:49.488433408   
order_item_count          107855.0                       1.098085   
payment_value             107855.0                     157.581275   

                                          min                  25%  \
order_purchase_timestamp  2016-09-04 21:15:19  2017-09-10 10:14:46   
order_item_count                          1.0                  1.0   
payment_value                             0.0                57.75   

                                          50%                         75%  \
order_purchase_timestamp  2018-01-17 10:53:02  2018-05-03 19:48:53.500000   
order_item_count                          1.0                         1.0   
payment_value                          102.26                      176.16   

                                          max         std  
order_purchase_timestamp  2018-10-17 17:30:18         NaN  
order_item_count                         20.0    0.450956  
payment_value                        13664.08  219.930545

In [5]:
customer_activity[customer_activity.duplicated(subset=["order_id"], keep=False)].head()

customer_unique_id                       customer_id  \
28  df2988ba3ed226b10521a0e4da849b61  16e14c1e6e050fe6730c961ff638ca23   
29  df2988ba3ed226b10521a0e4da849b61  16e14c1e6e050fe6730c961ff638ca23   
30  df2988ba3ed226b10521a0e4da849b61  16e14c1e6e050fe6730c961ff638ca23   
31  df2988ba3ed226b10521a0e4da849b61  16e14c1e6e050fe6730c961ff638ca23   
32  df2988ba3ed226b10521a0e4da849b61  16e14c1e6e050fe6730c961ff638ca23   

                            order_id order_status order_purchase_timestamp  \
28  63638a6806d67773f3adba8534553fff    delivered      2016-10-04 13:22:56   
29  63638a6806d67773f3adba8534553fff    delivered      2016-10-04 13:22:56   
30  63638a6806d67773f3adba8534553fff    delivered      2016-10-04 13:22:56   
31  63638a6806d67773f3adba8534553fff    delivered      2016-10-04 13:22:56   
32  63638a6806d67773f3adba8534553fff    delivered      2016-10-04 13:22:56   

    payment_sequential  payment_value  order_item_count  
28                 1.0          15.10               1.0  
29                 2.0          11.99               1.0  
30                 3.0           9.02               1.0  
31                 4.0          10.56               1.0  
32                 5.0          34.19               1.0

In [6]:
customer_activity = customer_activity.groupby(["customer_unique_id", "customer_id", "order_id", "order_status", "order_purchase_timestamp", "order_item_count"], as_index=False)[["payment_value"]].agg("sum").sort_values(by=["order_purchase_timestamp", "order_id"], ignore_index=True)
customer_activity.describe().T

count                           mean  \
order_purchase_timestamp    99441  2017-12-31 08:43:12.776581120   
order_item_count          99441.0                       1.140626   
payment_value             99441.0                      160.99009   

                                          min                  25%  \
order_purchase_timestamp  2016-09-04 21:15:19  2017-09-12 14:46:19   
order_item_count                          1.0                  1.0   
payment_value                             0.0                62.01   

                                          50%                  75%  \
order_purchase_timestamp  2018-01-18 23:04:36  2018-05-04 15:42:16   
order_item_count                          1.0                  1.0   
payment_value                          105.29               176.97   

                                          max         std  
order_purchase_timestamp  2018-10-17 17:30:18         NaN  
order_item_count                         21.0    0.536495  
payment_value                        13664.08  221.950148

In [7]:
max_date = customer_activity["order_purchase_timestamp"].max() + datetime.timedelta(1)
rfm_data = customer_activity.groupby("customer_unique_id", as_index=False).agg(
    recency =  ("order_purchase_timestamp", lambda x: (max_date-x.max()).days),
    frequency = ("order_id", lambda x: x.nunique()),
    monetary =  ("payment_value", "sum"),
    avg_spend = ("payment_value", "mean")
)
rfm_data.describe().T

count        mean         std  min     25%     50%     75%  \
recency    96096.0  288.735691  153.414676  1.0  164.00  269.00  398.00   
frequency  96096.0    1.034809    0.214384  1.0    1.00    1.00    1.00   
monetary   96096.0  166.593985  231.427720  0.0   63.12  108.00  183.53   
avg_spend  96096.0  161.401609  222.306928  0.0   62.46  105.83  177.21   

                max  
recency      773.00  
frequency     17.00  
monetary   13664.08  
avg_spend  13664.08

### Feature Engineering

#### Robust Scaler

In [8]:
scaler = RobustScaler()
rfm_scaled = scaler.fit_transform(rfm_data[["recency", "frequency", "monetary"]])

In [9]:
tmp = pd.DataFrame(rfm_scaled)
tmp.columns = ["recency", "frequency", "monetary"]
tmp.describe().T

count      mean       std       min       25%  50%       75%  \
recency    96096.0  0.084341  0.655618 -1.145299 -0.448718  0.0  0.551282   
frequency  96096.0  0.034809  0.214384  0.000000  0.000000  0.0  0.000000   
monetary   96096.0  0.486621  1.921998 -0.896935 -0.372727  0.0  0.627273   

                  max  
recency      2.153846  
frequency   16.000000  
monetary   112.582676

### K-Means Clustering

In [10]:
def elbow_clusters(k, data):
    cluster_values = list(range(1,k+1))
    inertias = []
    for c in cluster_values:
        model = KMeans(n_clusters=c, init="k-means++", max_iter=400, random_state=0)
        model.fit(data)
        inertias.append(model.inertia_)
    return inertias

In [11]:
def silhouette_clusters(k, data):
    cluster_values = list(range(2,k+1))
    scores = []
    for c in cluster_values:
        model = KMeans(n_clusters=c, init="k-means++", max_iter=400, random_state=0)
        model.fit(data)
        labels = model.labels_
        scores.append(silhouette_score(data, labels, metric="euclidean"))
    return scores

#### Robust Scaled

In [12]:
outputs = elbow_clusters(k=12, data=rfm_scaled)
distances = pd.DataFrame({"clusters": list(range(1,13)), "sum_of_squared_distances": outputs})

figure = go.Figure()
figure.add_trace(go.Scatter(x=distances["clusters"], y=distances["sum_of_squared_distances"]))
figure.update_layout(xaxis = dict(tick0=1, dtick=1, tickmode="linear"),
                  xaxis_title = "Number of clusters",
                  yaxis_title = "Sum of squared distances",
                  title_text = "Finding optimal number of clusters using elbow method")
figure.show()

In [13]:
outputs = silhouette_clusters(k=8, data=rfm_scaled)
scores = pd.DataFrame({"clusters": list(range(2,9)), "silhouette_score": outputs})

figure = go.Figure()
figure.add_trace(go.Scatter(x=scores["clusters"], y=scores["silhouette_score"]))
figure.update_layout(xaxis = dict(tick0=1, dtick=1, tickmode="linear"),
                  xaxis_title = "Number of clusters",
                  yaxis_title = "Silhouette score",
                  title_text = "Finding optimal number of clusters using silhouette score")
figure.show()

In [18]:
n_clusters = 4
kmeans_model = KMeans(n_clusters=n_clusters, init="k-means++", max_iter=400, random_state=0)
kmeans_model.fit_predict(rfm_scaled)
rfm_data["clusters"] = kmeans_model.labels_
rfm_data["clusters"] = rfm_data["clusters"].astype("category")

figure = px.scatter_3d(rfm_data,
                    color="clusters",
                    x="recency",
                    y="frequency",
                    z="monetary",
                    #category_orders = {"clusters": ["0", "1", "2", "3"]}
                    )
figure.update_layout()
figure.show()

### RFM Segmentation

In [15]:
rfm_data.describe().T

count        mean         std  min     25%     50%     75%  \
recency    96096.0  288.735691  153.414676  1.0  164.00  269.00  398.00   
frequency  96096.0    1.034809    0.214384  1.0    1.00    1.00    1.00   
monetary   96096.0  166.593985  231.427720  0.0   63.12  108.00  183.53   
avg_spend  96096.0  161.401609  222.306928  0.0   62.46  105.83  177.21   

                max  
recency      773.00  
frequency     17.00  
monetary   13664.08  
avg_spend  13664.08

In [16]:
r_labels = range(4,0,-1)
r_quartiles = pd.qcut(rfm_data["recency"], 4, labels=r_labels)

m_labels = range(1,5)
m_quartiles = pd.qcut(rfm_data["monetary"], 4, labels=m_labels)

rfm_data["R"] = r_quartiles.values
rfm_data["M"] = m_quartiles.values

def segment_F(x):
    if x == 1:
        return 1
    elif x == 2:
        return 2
    elif x == 3:
        return 3
    else:
        return 4

rfm_data["F"] = rfm_data["frequency"].apply(segment_F).astype("category")

In [20]:
rfm_data.head()

customer_unique_id  recency  frequency  monetary  avg_spend  \
0  0000366f3b9a7992bf8c76cfdf3221e2      161          1    141.90     141.90   
1  0000b849f77a49e4a4ce2b2a4ca5be3f      164          1     27.19      27.19   
2  0000f46a3911fa3c0805444483337064      586          1     86.22      86.22   
3  0000f6ccb0745a6a4b88665a16c9f078      370          1     43.62      43.62   
4  0004aac84e0df4da2b147fca70cf8255      337          1    196.89     196.89   

  clusters  R  M  F  RFM  
0        0  4  3  1  413  
1        0  4  1  1  411  
2        0  1  2  1  112  
3        0  2  1  1  211  
4        0  2  4  1  214

In [21]:
rfm_data["RFM"] = rfm_data["R"].astype(str) + rfm_data["F"].astype(str) + rfm_data["M"].astype(str)
rfm_data.groupby("RFM", as_index=False).agg({
    "recency" : "mean",
    "frequency" : "mean",
    "monetary" : "mean",
    "RFM" : "count"
}).round(2)

recency  frequency  monetary   RFM
0    505.88       1.00     43.77  6121
1    498.49       1.00     83.63  6170
2    505.27       1.00    140.23  5536
3    505.95       1.00    406.27  5512
4    530.29       2.00     49.21    14
5    505.24       2.00     85.61    71
6    491.00       2.00    144.15   159
7    485.56       2.00    420.98   326
8    651.00       3.00     51.86     2
9    566.50       3.00     88.30     2
10   446.29       3.00    152.26     7
11   480.83       3.00    383.02    29
12   651.00       4.00     73.48     1
13   604.00       5.00    121.26     2
14   514.00       4.00    742.92     2
15   327.68       1.00     43.89  5922
16   328.15       1.00     83.93  6126
17   327.94       1.00    142.02  5795
18   329.15       1.00    387.94  5496
19   351.56       2.00     53.41     9
20   328.01       2.00     90.22    78
21   330.38       2.00    142.31   188
22   327.71       2.00    418.35   406
23   287.00       3.00     87.60     1
24   353.00       3.00    147.56     2
25   334.76       3.00    611.68    38
26   338.83       4.33    659.68     6
27   218.57       1.00     43.51  5991
28   216.73       1.00     83.45  5748
29   216.23       1.00    142.19  5942
30   215.74       1.00    381.56  5534
31   212.60       2.00     47.78    15
32   217.01       2.00     87.92    72
33   218.84       2.00    146.94   183
34   220.51       2.00    383.46   454
35   216.08       3.00    157.32    12
36   209.22       3.00    431.13    45
37   210.40       5.13    712.83    15
38   105.93       1.00     43.40  5936
39   106.40       1.00     83.90  5685
40   108.19       1.00    140.99  5991
41   108.21       1.00    404.04  5594
42   103.80       2.00     51.64    15
43   109.94       2.00     88.43    82
44   105.10       2.00    146.61   188
45   106.85       2.00    401.43   485
46    52.00       3.00     88.27     1
47   101.75       3.00    144.94     8
48   100.05       3.00    669.30    56
49   102.22       5.13    961.61    23